#Introdution to Dataset
This lab uses 2 dataset
## VLSP 2016 - Vietnamese Automatic Speech Recognition 
* The dataset has 3 labels: 
  + positive: 1
  + neutral: 0
  + negative: -1
* Train data has 5100 train samples và 1050 test sample

## AIVIVN 
 https://github.com/tuanpham1989/sentiment_analysis_nal/tree/master/data_clean
* The dataset has 2 labels (classes)
  + postive: 1
  + negative: - 1

* Dataset has 16087 train samples and 10981 test samples. But labels of tests data were hidden. So we just use the train data.

# Install and import required libs


In [ ]:

!pip install pyvi
import tensorflow as tf
import pandas as pd 
import numpy as np
from string import digits
from collections import Counter
from pyvi import ViTokenizer
from gensim.models.word2vec import Word2Vec
from keras.utils.np_utils import to_categorical
%matplotlib inline


# Load train and test dataset

## Preprocess the added dataset

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

import re

correct_mapping = {
    "ship": "vận chuyển",
    "shop": "cửa hàng",
    "m": "mình",
    "mik": "mình",
    "ko": "không",
    "k": " không ",
    "kh": "không",
    "khong": "không",
    "kg": "không",
    "khg": "không",
    "tl": "trả lời",
    "r": "rồi",
    "fb": "mạng xã hội", # facebook
    "face": "mạng xã hội",
    "thanks": "cảm ơn",
    "thank": "cảm ơn",
    "tks": "cảm ơn",
    "tk": "cảm ơn",
    "ok": "tốt",
    "dc": "được",
    "vs": "với",
    "đt": "điện thoại",
    "thjk": "thích",
    "qá": "quá",
    "trể": "trễ",
    "bgjo": "bao giờ"
}


def tokmap(tok):
    if tok.lower() in correct_mapping:
        return correct_mapping[tok.lower()]
    else:
        return tok


def preprocess(review):
    tokens = review.split()
    tokens = map(tokmap, tokens)
    return " ".join(tokens)


def load_data(filepath, is_train=True):
    regex = 'train_'
    if not is_train:
        regex = 'test_'

    a = []
    b = []

    with open(filepath, "r", encoding="utf-8", errors="ignore") as f:
        for line in f:
            line = line.strip()
            if regex in line:
                b.append(a)
                a = [line]
            elif line != "":
                a.append(line)

        b.append(a)

    b = b[1:]
    lst = []
    for tp in b:
        idx = tp[0]
        if is_train:
            lb = int(tp.pop(-1))
        else:
            lb = "0"
        review = " ".join(tp[1:])
        review = re.sub(r"^\"*", "", review)
        review = re.sub(r"\"*$", "", review)
        review_ = preprocess(review)
        lst.append([idx, review, review_, lb])
    return lst


TRAIN_FILE = "/content/drive/MyDrive/Learning/Natural Language Processing/Exercises/Bai Tap Lon/augment_data/train.crash.txt"
TEST_FILE = "/content/drive/MyDrive/Learning/Natural Language Processing/Exercises/Bai Tap Lon/augment_data/test.crash.txt"

TRAIN_CSV = "/content/drive/MyDrive/Learning/Natural Language Processing/Exercises/Bai Tap Lon/augment_data/train_augment.csv"
TEST_CSV = "/content/drive/MyDrive/Learning/Natural Language Processing/Exercises/Bai Tap Lon/augment_data/test_augment.csv"

train_data = load_data(TRAIN_FILE)
test_data = load_data(TEST_FILE, is_train=False)

print("# Loaded training samples: {}".format(len(train_data)))

cols = ["id", "text", "text_ws", "label"]
df_train = pd.DataFrame(data=train_data, columns=cols)

df_train = df_train[['label', 'text_ws']]
df_train.rename({'label': 'Class', 'text_ws': 'Data'}, axis=1, inplace=True)
df_train['Class'] = df_train['Class'].map({0: 1, 1: -1})
df_train.to_csv(TRAIN_CSV, index=False)



Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).
# Loaded training samples: 16087


In [ ]:
from google.colab import drive
drive.mount('/content/drive')

def read_train_data():
  data_train = pd.read_csv("/content/drive/MyDrive/Learning/Natural Language Processing/Exercises/Bai Tap Lon/vlsp_sentiment_train.csv", sep='\t')
  data_train.columns =['Class', 'Data']

  data_aug = pd.read_csv(TRAIN_CSV)
  data_train = pd.concat((data_train, data_aug))

  data_test = pd.read_csv("/content/drive/MyDrive/Learning/Natural Language Processing/Exercises/Bai Tap Lon/vlsp_sentiment_test.csv", sep='\t')
  data_test.columns =['Class', 'Data'] 
  return data_train, data_test

data_train, data_test = read_train_data()



Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


# Preprocess data

In [ ]:
print(data_train.shape)
print(data_test.shape)

(21187, 2)
(1050, 2)


In [ ]:
labels = data_train.iloc[:, 0].values
reviews = data_train.iloc[:, 1].values

In [ ]:
def encode_labels(labels):
  result = []
  for label in labels:
      if label == -1:
          result.append([1,0,0])
      elif label == 0:
          result.append([0,1,0])
      else:
          result.append([0,0,1])

  return np.array(result)  

encoded_labels = encode_labels(labels)

In [ ]:
def remove_digits(reviews_input):
  result=[]
  for review in reviews_input:
      review_cool_one = ''.join([char for char in review if char not in digits])
      result.append(review_cool_one)
  return result

reviews_processed = remove_digits(reviews)
print(reviews_processed)
unlabeled_processed = [] 


['Mình đã dùng anywhere thế hệ đầu, quả là đầy thất vọng, hiện tại đang vứt xó. Giá thì đắt, ngốn pin như ăn gỏi, nặng', 'Quan tâm nhất là độ trễ có cao không, dùng thi thoảng nó cứ trễ bực mình, đấy mới chỉ là dùng văn phòng chứ game thì chắc là ném đi từ lâu. Không biết con này có độ trễ không nhỉ. Dùng nhiều loại nhưng vẫn kết nhất con chuột sứ mitsumi, gọn bấm nảy tốt', 'dag xài con cùi bắp k....pin trâu, mỗi tội đánh liên minh ức chế đập hết  con', 'logitech chắc hàng phải tiền triệu trở lên dùng mới thích chứ em dùng con có k thấy được vài bữa là hư. chuyển sang eblue dùng được hơn năm chưa thấy hỏng.', 'Đang xài con m cùi mía , nhà xài nhiều chuột nên thử con này con kia chơi và kết quả là sau  tháng và  con chuột khác nhau đủ kiểu đa chức năng mà h chỉ còn lại là con m cùi mía còn xài dc : h đi mua chuột là xác định ko để mấy con nhân viên vấy ngắn nó dụ nửa cứ logitech mà fan', 'Đang xài  con M, nút chuột giữa hai con đều như hạch. xài chưa được năm , scroll đã chạy bậy rồi. H

In [ ]:

#Use PyVi for Vietnamese word tokenizer
all_words = []
def tokenize(reviews_processed_input):
  result = []
  for review in reviews_processed_input:
      review = ViTokenizer.tokenize(review.lower())
      result.append(review.split())
  return result

word_reviews =  tokenize(reviews_processed)
print(word_reviews)
   

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [ ]:
EMBEDDING_DIM = 400 # how big is each word vector
MAX_VOCAB_SIZE = 10000 # how many unique words to use (i.e num rows in embedding vector)
MAX_SEQUENCE_LENGTH = 300 # max number of words in a comment to use

In [ ]:
from keras.preprocessing.text import Tokenizer
from keras.preprocessing.sequence import pad_sequences
from tensorflow.keras.utils import to_categorical

In [ ]:
tokenizer = Tokenizer(num_words=MAX_VOCAB_SIZE, lower=True, char_level=False)
#get word index sequence,word index,
def pre_process(tokenizer_words, tokenizer):
    tokenizer.fit_on_texts(tokenizer_words)    
    return tokenizer.texts_to_sequences(tokenizer_words), tokenizer.word_index

sequences_train, word_index = pre_process(word_reviews, tokenizer)

print(sequences_train)
print(word_index)


[[13, 38, 29, 3165, 1148, 176, 5, 787, 11, 550, 151, 5, 722, 128, 852, 2141, 1, 49, 12, 347, 5, 1681, 101, 32, 7692, 5, 578], [891, 149, 11, 273, 1360, 10, 205, 3, 5, 29, 4856, 69, 190, 1360, 1187, 5, 329, 50, 55, 11, 29, 1995, 136, 400, 12, 145, 11, 1857, 77, 124, 163, 1, 3, 80, 70, 30, 10, 273, 1360, 3, 310, 1, 29, 59, 248, 20, 72, 952, 149, 70, 373, 4239, 4857, 5, 703, 603, 4240, 17], [2776, 100, 70, 892, 1583, 113, 48, 1, 101, 893, 5, 228, 551, 635, 3759, 2142, 1188, 102, 70], [1189, 145, 6, 53, 28, 401, 1361, 89, 29, 50, 97, 136, 88, 29, 70, 10, 113, 46, 18, 298, 1277, 11, 342, 1, 422, 357, 7693, 29, 18, 39, 188, 57, 46, 319, 1], [128, 100, 70, 360, 892, 3760, 5, 221, 100, 59, 373, 43, 214, 70, 30, 70, 540, 328, 7, 909, 11, 95, 260, 7, 70, 373, 108, 265, 242, 257, 1792, 545, 19, 366, 55, 47, 37, 11, 70, 360, 892, 3760, 47, 100, 469, 62, 366, 77, 16, 373, 11, 2343, 87, 61, 122, 70, 661, 5844, 853, 69, 3438, 760, 190, 1189, 19, 733], [128, 100, 70, 360, 5, 396, 373, 876, 324, 70, 21

In [ ]:
#padding with max length
data = pad_sequences(sequences_train, maxlen=MAX_SEQUENCE_LENGTH)
labels = encoded_labels

In [ ]:
print('Shape of X train and X validation tensor:',data.shape)
print('Shape of label train and validation tensor:', labels.shape)

Shape of X train and X validation tensor: (21187, 300)
Shape of label train and validation tensor: (21187, 3)


# Build and train model

* Tầng Input: đầu vào là vector onehop có 300 chiều
* Tầng Embedding: chuyển vector input thành vector embedding bằng ma trận trọng số 300x400. Tổng số params cần học: 

In [ ]:
import gensim
from gensim.models import Word2Vec
from gensim.utils import simple_preprocess

from gensim.models.keyedvectors import KeyedVectors
from keras.layers import Embedding

def build_embedding_layer(word_index):

  word_vectors = KeyedVectors.load_word2vec_format('/content/drive/MyDrive/Learning/Natural Language Processing/Exercises/Bai Tap Lon/vi-model-CBOW.bin', binary=True)
  vocabulary_size=min(len(word_index)+1,MAX_VOCAB_SIZE)
  embedding_matrix = np.zeros((vocabulary_size, EMBEDDING_DIM))
  for word, i in word_index.items():
      if i>=MAX_VOCAB_SIZE:
          continue
      try:
          embedding_vector = word_vectors[word]
          embedding_matrix[i] = embedding_vector
      except KeyError:
          embedding_matrix[i]=np.random.normal(0,np.sqrt(0.25),EMBEDDING_DIM)

  del(word_vectors)


  return Embedding(vocabulary_size, EMBEDDING_DIM,weights=[embedding_matrix], trainable=True)


embedding_layer = build_embedding_layer(word_index)

In [ ]:
from keras.layers import Dense, Input, GlobalMaxPooling1D
from keras.layers import Conv1D, MaxPooling1D, Embedding
from keras.models import Model
from keras.layers import Input, Dense, Embedding, Conv2D, MaxPooling2D, Dropout,concatenate
from keras.layers.core import Reshape, Flatten
from keras.callbacks import EarlyStopping
from tensorflow.keras.optimizers import Adam

from keras.models import Model
from keras import regularizers

from keras.layers import Dense, Input, GlobalMaxPooling1D
from keras.layers import Conv1D, MaxPooling1D, Embedding
from keras.models import Model
from keras.layers import Input, Dense, Embedding, Conv2D, MaxPooling2D, Dropout,concatenate
from keras.layers.core import Reshape, Flatten
from keras.callbacks import EarlyStopping
from tensorflow.keras.optimizers import Adam
from keras.models import Model
from keras import regularizers
from keras.metrics import Precision
from keras.metrics import Recall


def build_model(sequence_length, embedding_layer):
  filter_sizes = [3,4,5]
  num_filters = 100
  drop = 0.5

  inputs = Input(shape=(sequence_length,))
  embedding = embedding_layer(inputs)
  reshape = Reshape((sequence_length,EMBEDDING_DIM,1))(embedding)

  conv_0 = Conv2D(num_filters, (filter_sizes[0], EMBEDDING_DIM),activation='relu',kernel_regularizer=regularizers.l2(0.01))(reshape)
  conv_1 = Conv2D(num_filters, (filter_sizes[1], EMBEDDING_DIM),activation='relu',kernel_regularizer=regularizers.l2(0.01))(reshape)
  conv_2 = Conv2D(num_filters, (filter_sizes[2], EMBEDDING_DIM),activation='relu',kernel_regularizer=regularizers.l2(0.01))(reshape)

  maxpool_0 = MaxPooling2D((sequence_length - filter_sizes[0] + 1, 1), strides=(1,1))(conv_0)
  maxpool_1 = MaxPooling2D((sequence_length - filter_sizes[1] + 1, 1), strides=(1,1))(conv_1)
  maxpool_2 = MaxPooling2D((sequence_length - filter_sizes[2] + 1, 1), strides=(1,1))(conv_2)

  merged_tensor = concatenate([maxpool_0, maxpool_1, maxpool_2], axis=1)
  flatten = Flatten()(merged_tensor)
  reshape = Reshape((3*num_filters,))(flatten)
  dropout = Dropout(drop)(flatten)
  output = Dense(units=3, activation='softmax',kernel_regularizer=regularizers.l2(0.01))(dropout)


  # this creates a model that includes
  cnn = Model(inputs, output)


  adam = Adam(learning_rate=0.001, beta_1=0.9, beta_2=0.999, epsilon=1e-08, decay=0.0)
  cnn.compile(loss='categorical_crossentropy', optimizer=adam, metrics=['accuracy', Precision(), Recall()])
  cnn.summary()
  return cnn

#define callbacks
early_stopping = EarlyStopping(monitor='val_loss', min_delta=0.01, patience=4, verbose=1)
callbacks_list = [early_stopping]

model = build_model(data.shape[1], embedding_layer)



Model: "model"
__________________________________________________________________________________________________
 Layer (type)                   Output Shape         Param #     Connected to                     
 input_1 (InputLayer)           [(None, 300)]        0           []                               
                                                                                                  
 embedding (Embedding)          (None, 300, 400)     4000000     ['input_1[0][0]']                
                                                                                                  
 reshape (Reshape)              (None, 300, 400, 1)  0           ['embedding[0][0]']              
                                                                                                  
 conv2d (Conv2D)                (None, 298, 1, 100)  120100      ['reshape[0][0]']                
                                                                                              

#input: one hop 300,  vector 300 , 
vecctor one [tong so tu] => 290, vector one hop * emdding 300 x 400
=> 300 x 400

# reshape, them 1 chieu 300x400x1, khong  trong so

# convonution 1: 100 filters, cua so 3x400 , 
100 cua so  4x400,  100 filter 5*400

##CONV 1so luong parameters : kernel size (3* 400 * 100 + 1 bias) * filter size 
## CONV 2:  so luong parameters : kernel size (4* 400 + 1 bias) * 100 filter size
## CONV 3so luong parameters : kernel size (5* 400 * 100 + 1 bias) * filter size 

# MAX  Pooling
# Concat hok them trong so, ra 1 ma tran 3x1x100
# flattent 1 vector 300 chieu,

# drop hok them tham so, 50% tham so

#Dense

3 node, 300 + 1 bias * 3)





In [ ]:

history = model.fit(data, labels, validation_split=0.2,
          epochs=10, batch_size=256,callbacks=callbacks_list, shuffle=True, verbose=2)

Epoch 1/10
67/67 - 479s - loss: 0.8805 - accuracy: 0.7279 - precision: 0.7789 - recall: 0.6611 - val_loss: 0.5023 - val_accuracy: 0.8844 - val_precision: 0.9006 - val_recall: 0.8596 - 479s/epoch - 7s/step
Epoch 2/10
67/67 - 472s - loss: 0.6655 - accuracy: 0.8016 - precision: 0.8407 - recall: 0.7567 - val_loss: 0.5020 - val_accuracy: 0.8846 - val_precision: 0.9030 - val_recall: 0.8608 - 472s/epoch - 7s/step
Epoch 3/10


# Plot data

In [ ]:
import pandas as pd
import matplotlib.pyplot as plt

def show_graph(history):
  pd.DataFrame(history.history).plot(figsize = (16, 10))
  plt.grid(True)
  plt.gca().set_ylim(0, 1)
  plt.xlabel('Epoch')
  plt.ylabel('Score')
  plt.show()

show_graph(history)

# Evaluate model

In [ ]:
labels_test = data_test.iloc[:, 0].values
reviews_test = data_test.iloc[:, 1].values

In [ ]:
encoded_labels_test = encode_labels(labels_test)
print(encoded_labels_test)

In [ ]:
unlabeled_processed_test = [] 
reviews_processed_test = remove_digits(reviews_test)
print(reviews_processed_test)


In [ ]:
#Use PyVi for Vietnamese word tokenizer
word_reviews_test = []
all_words = []

word_reviews_test = tokenize(reviews_processed_test)
print(word_reviews_test)

In [ ]:
sequences_test = tokenizer.texts_to_sequences(word_reviews_test)
data_test = pad_sequences(sequences_test, maxlen=MAX_SEQUENCE_LENGTH)
labels_test = encoded_labels_test

In [ ]:
print('Shape of X train and X validation tensor:',data_test.shape)
print('Shape of label train and validation tensor:', labels_test.shape)

In [ ]:
score = model.evaluate(data_test, labels_test)

# Performance của model

In [ ]:
print("%s: %.2f%%" % (model.metrics_names[0], score[0]*100))
print("%s: %.2f%%" % (model.metrics_names[1], score[1]*100))
print("%s: %.2f%%" % (model.metrics_names[2], score[2]*100))
print("%s: %.2f%%" % (model.metrics_names[3], score[3]*100))



# Test model

## Review 5*

In [ ]:
test = "Áo hơi mỏng nhưng rất đẹp hình thêu các thứ rất đẹp còn 1 vài chỗ có chỉ thừa phần 2 túi áo nên làm kiểu zip chất lương hơn tí hoặc có thể k cần zip cũng đc phần bo chun ống tay và cổ áo cần cải thiện thêm. Nói chung với giá đc sale xuống và mình dùng voucher nữa nên như này mình cũng hài lòng rồi"
reviews_processed_test = []

review_not_contain_digit = ''.join([char for char in test if char not in digits])
reviews_processed_test.append(review_not_contain_digit)

word_reviews_test = tokenize(reviews_processed_test)


tokenizer = Tokenizer(num_words=MAX_VOCAB_SIZE, lower=True, char_level=False)
tokenizer.fit_on_texts(word_reviews_test)
sequences_train = tokenizer.texts_to_sequences(word_reviews_test)

sampleToPredit = pad_sequences(sequences_train, maxlen=MAX_SEQUENCE_LENGTH)

class_names = ["Negative", "Neutral", "Positive"]
pre = model.predict(sampleToPredit)
print(pre)
print(class_names[np.argmax(pre)])


## Review 3*

In [ ]:
test = "Áo mỏng hơn so với mình nghĩ.... Ko xứng đáng với giá 450k sz L mà như M vậy"

reviews_processed_test = []

review_not_contain_digit = ''.join([char for char in test if char not in digits])
reviews_processed_test.append(review_not_contain_digit)


word_reviews_test = tokenize(reviews_processed_test)
print(word_reviews_test)
sequences_train, word_index = pre_process(word_reviews_test, tokenizer)
print(word_reviews_test)

sampleToPredit = pad_sequences(sequences_train, maxlen=MAX_SEQUENCE_LENGTH)

pre = model.predict(sampleToPredit)
print(pre)
print(class_names[np.argmax(pre)])

## Review 1*

In [ ]:
test = "Như cái rẻ lau chân chán kinh khủng, mua phí tiền.mặc được chết liền"

reviews_processed_test = []

review_not_contain_digit = ''.join([char for char in test if char not in digits])
reviews_processed_test.append(review_not_contain_digit)


word_reviews_test = tokenize(reviews_processed_test)
print(word_reviews_test)
sequences_train, word_index = pre_process(word_reviews_test, tokenizer)
print(word_reviews_test)

sampleToPredit = pad_sequences(sequences_train, maxlen=MAX_SEQUENCE_LENGTH)

pre = model.predict(sampleToPredit)
print(pre)
print(class_names[np.argmax(pre)])